# フォルダ名の変更

# 欠陥名当て用データ作成

## フォルダの選別
1. 子フォルダ内の画像枚数が0枚→子フォルダを削除
2. 子フォルダ数が0→親フォルダを削除

※ 子フォルダ名を "None" or "欠陥"にしておく

In [85]:
# ベースパス
base_folder = "/home/dataset/yyama_dataset/AC_images"

In [82]:
import os
import shutil

def delete_folder(folder_path):
    try:
        shutil.rmtree(folder_path)
    except Exception as e:
        print(f"エラー：{e}")

def count_image_files(folder_path):
    image_extensions = ['.jpg', '.jpeg', '.png']
    image_count = 0
    for file in os.listdir(folder_path):
        if any(file.lower().endswith(ext) for ext in image_extensions):
            image_count += 1
    return image_count

if os.path.isdir(base_folder):  # ベースフォルダが存在するかチェック
    for parent_folder in os.listdir(base_folder):
        parent_folder_path = os.path.join(base_folder, parent_folder)
        if os.path.isdir(parent_folder_path):  # parent_folder_pathがディレクトリであるかチェック
            for child_folder in os.listdir(parent_folder_path):
                child_folder_path = os.path.join(parent_folder_path, child_folder)
                if os.path.isdir(child_folder_path):  # child_folder_pathがディレクトリであるかチェック
                    num_images = count_image_files(child_folder_path)
                    if num_images == 0:
                        print(f"削除フォルダ名: {child_folder_path}, 枚数: {num_images}")
                        delete_folder(child_folder_path)
            if len(os.listdir(parent_folder_path)) == 0:
                print(f"削除フォルダ名: {parent_folder_path}")
                delete_folder(parent_folder_path)

#### 拡張子を除いたフォルダ名の重複を修正<br>
punctured_tire内に"image_49.jpeg"と"image_49.jpg"が存在したため、全てチェックする

In [83]:
import os
import re

# ベースフォルダが存在するかどうかを確認
if os.path.isdir(base_folder):
    # 親フォルダ内のサブフォルダを取得
    for folder_name in os.listdir(base_folder):
        subfolder_path = os.path.join(base_folder, folder_name)
        
        if os.path.isdir(subfolder_path):  # サブフォルダであるか確認
            # サブフォルダ内の子フォルダを取得
            for subfolder_name in os.listdir(subfolder_path):
                child_folder_path = os.path.join(subfolder_path, subfolder_name)
                
                if os.path.isdir(child_folder_path):  # 子フォルダであるか確認
                    # 子フォルダ内のファイル名を取得
                    files = os.listdir(child_folder_path)
                    
                    # ファイル名から数字部分を取得し、リストに保存
                    numbers = [int(re.search(r'\d+', file).group()) for file in files if re.search(r'\d+', file)]
                    
                    # ファイル名の重複チェックと変更
                    for file in files:
                        match = re.search(r'\d+', file)
                        if match:
                            number = int(match.group())
                            
                            # 同じ番号が複数存在する場合
                            if numbers.count(number) > 1:
                                new_number = 0
                                
                                # 重複していない番号を探す
                                while new_number in numbers:
                                    new_number += 1
                                
                                # 新しいファイル名を作成
                                new_file = file.replace(str(number), str(new_number))
                                new_file_path = os.path.join(child_folder_path, new_file)
                                
                                # ファイル名を変更
                                os.rename(
                                    os.path.join(child_folder_path, file), 
                                    new_file_path
                                )
                                
                                # ファイル名の変更を表示
                                print(f'{child_folder_path}/{file} -> {new_file_path}')
                                
                                # リストを更新
                                numbers.remove(number)
                                numbers.append(new_number)

train：val = 8：2 に分ける

In [86]:
import os
import shutil
import random

# ディレクトリのパスを指定

src_dir = "/home/dataset/yyama_dataset/AC_images"
train_dir = '/home/dataset/yyama_dataset/tasks/AC/train/'
val_dir = '/home/dataset/yyama_dataset/tasks/AC/val/'

# trainとvalの割合
ratio = 0.8

# trainとvalのディレクトリを作成
os.makedirs(train_dir, exist_ok=True)
os.makedirs(val_dir, exist_ok=True)

# src_dir内の各フォルダに対して
for root, dirs, files in os.walk(src_dir):
    # 画像のリストを取得し、シャッフル
    images = [f for f in files if os.path.isfile(os.path.join(root, f))]
    random.shuffle(images)
    
    # trainとvalに分割
    train_images = images[:int(ratio * len(images))]
    val_images = images[int(ratio * len(images)):]
    # print(len(train_images))
    # print(len(val_images))
    
    # trainとvalのサブディレクトリを作成
    # print(os.path.join(train_dir, os.path.relpath(root, src_dir)))
    train_folder = os.path.join(train_dir, os.path.relpath(root, src_dir))
    val_folder = os.path.join(val_dir, os.path.relpath(root, src_dir))
    os.makedirs(train_folder, exist_ok=True)
    os.makedirs(val_folder, exist_ok=True)
    
    # # 画像をコピー
    for img in train_images:
        shutil.copy(os.path.join(root, img), os.path.join(train_folder, img))
        # print(os.path.join(root, img))
        # print(os.path.join(train_folder, img))
    for img in val_images:
        shutil.copy(os.path.join(root, img), os.path.join(val_folder, img))
        # print(os.path.join(root, img))
        # print(os.path.join(val_folder, img))

print('Images copied to train and val folders.')

Images copied to train and val folders.


val中の画像枚数が1の子フォルダをtrainへ移動

In [92]:
import os
import shutil
from pathlib import Path
# 子フォルダを移動させる関数
def move_child_folder(src, dst):
    """
    :param src: 移動するフォルダのパス
    :param dst: 移動先のパス
    """ 
    if os.path.exists(dst):
        # 移動先のディレクトリが存在する場合、ファイルのみを移動
        for file_name in os.listdir(src):
            full_file_name = os.path.join(src, file_name)
            if os.path.isfile(full_file_name):
                shutil.move(full_file_name, dst)
        # もとのフォルダを削除
        os.rmdir(src)
    else:
        # 移動先のフォルダが存在しない場合、フォルダごと移動
        if not os.path.exists(os.path.dirname(dst)):
            os.makedirs(os.path.dirname(dst))
        shutil.move(src, os.path.join(os.path.dirname(dst), os.path.basename(src)))

# 親フォルダごと移動させる関数
def move_parent_folder(src, dst):
    """
    :param src: 移動するフォルダのパス
    :param dst: 移動先のパス
    """
    for src_dir, dirs, files in os.walk(src):
        dst_dir = src_dir.replace(src, dst, 1)
        if not os.path.exists(dst_dir):
            os.makedirs(dst_dir)
        for file_ in files:
            src_file = os.path.join(src_dir, file_)
            dst_file = os.path.join(dst_dir, file_)
            if os.path.exists(dst_file):
                os.remove(dst_file)
            shutil.move(src_file, dst_dir)
    shutil.rmtree(src)
    
# 移動先のパスを生成する関数
def change_path(path, new_base):
    # パスを分割
    parts = path.split('/')
    # 新しいベースでパスを再構築
    parts[1] = new_base
    return '/'.join(parts)

# 与えられたフォルダ内の画像ファイル数を数える関数
def count_image_files(folder_path):
    image_extensions = ['.jpg', '.jpeg', '.png']  # 画像ファイルの拡張子を追加
    image_count = 0
    for file in os.listdir(folder_path):
        if any(file.lower().endswith(ext) for ext in image_extensions):
            image_count += 1
    return image_count

def val(val_dir, val_base):
    if os.path.isdir(val_dir):  # val_dirがディレクトリであるか確認
        for parent_folder in os.listdir(val_dir):
            parent_folder_path = os.path.join(val_dir, parent_folder)
            parent_dir_name = Path(parent_folder_path).name
            if os.path.isdir(parent_folder_path):  # ディレクトリであるか確認
                for child_folder in os.listdir(parent_folder_path):
                    child_folder_path = os.path.join(parent_folder_path, child_folder)
                    if os.path.isdir(child_folder_path):  # ディレクトリであるか確認
                        num_images = count_image_files(child_folder_path)
                        if num_images == 1:
                            # print(f'子フォルダ:{child_folder_path}')
                            print(f'親:{Path(child_folder_path).parent.name}    子:{Path(child_folder_path).name}')
                            print(f"移動フォルダ名: {child_folder_path}, 移動先: {val_base+Path(child_folder_path).parent.name+'/'+Path(child_folder_path).name}, 枚数: {num_images}")
                            move_child_folder(child_folder_path, val_base+Path(child_folder_path).parent.name+'/'+Path(child_folder_path).name)

val_dir = '/home/dataset/yyama_dataset/tasks/AC/val'
val_base = '/home/dataset/yyama_dataset/tasks/AC/train/'
val(val_dir, val_base)

親:acrylic_paint_on_canvas    子:crack
移動フォルダ名: /home/dataset/yyama_dataset/tasks/AC/val/acrylic_paint_on_canvas/crack, 移動先: /home/dataset/yyama_dataset/tasks/AC/train/acrylic_paint_on_canvas/crack, 枚数: 1
親:aluminum    子:fading
移動フォルダ名: /home/dataset/yyama_dataset/tasks/AC/val/aluminum/fading, 移動先: /home/dataset/yyama_dataset/tasks/AC/train/aluminum/fading, 枚数: 1
親:aluminum    子:warp
移動フォルダ名: /home/dataset/yyama_dataset/tasks/AC/val/aluminum/warp, 移動先: /home/dataset/yyama_dataset/tasks/AC/train/aluminum/warp, 枚数: 1
親:aluminum_can    子:dent
移動フォルダ名: /home/dataset/yyama_dataset/tasks/AC/val/aluminum_can/dent, 移動先: /home/dataset/yyama_dataset/tasks/AC/train/aluminum_can/dent, 枚数: 1
親:aluminum_foil    子:oxidation
移動フォルダ名: /home/dataset/yyama_dataset/tasks/AC/val/aluminum_foil/oxidation, 移動先: /home/dataset/yyama_dataset/tasks/AC/train/aluminum_foil/oxidation, 枚数: 1
親:aluminum_foil    子:pitting
移動フォルダ名: /home/dataset/yyama_dataset/tasks/AC/val/aluminum_foil/pitting, 移動先: /home/dataset/yyama_da

valとtrainから空のフォルダを削除

In [105]:
# 空のフォルダを削除
def delete_empty_folders(base_folder):
    if os.path.isdir(base_folder):
        for parent_folder in os.listdir(base_folder):
            parent_folder_path = os.path.join(base_folder, parent_folder)
            if os.path.isdir(parent_folder_path):  # ディレクトリであるか確認
                for child_folder in os.listdir(parent_folder_path):
                    child_folder_path = os.path.join(parent_folder_path, child_folder)
                    if os.path.isdir(child_folder_path):  # ディレクトリであるか確認
                        num_images = count_image_files(child_folder_path)
                        # 画像枚数が2枚未満の場合、その子フォルダを削除
                        if num_images==0:
                            print(f"削除フォルダ名: {child_folder_path}, 枚数: {num_images}")
                            delete_folder(child_folder_path)
                # 親フォルダ内の子フォルダ数が0の場合、親フォルダを削除
                if len(os.listdir(parent_folder_path))==0 :
                    print(f"削除フォルダ名: {parent_folder_path}")
                    delete_folder(parent_folder_path)
                    
train_dir = '/home/dataset/yyama_dataset/tasks/AC/train'
print(train_dir)
delete_empty_folders(train_dir)
val_dir = '/home/dataset/yyama_dataset/tasks/AC/val'
print(val_dir)
delete_empty_folders(val_dir)

/home/dataset/yyama_dataset/tasks/AC/train
/home/dataset/yyama_dataset/tasks/AC/val


In [94]:
import os

def find_missing_folders(folder1, folder2):
    """
    指定された2つのフォルダ間で存在しないフォルダを見つけて出力します。
    Args:
        folder1 (str): 最初のフォルダのパス
        folder2 (str): 2番目のフォルダのパス
    """
    # フォルダ1内のフォルダリストを取得
    folders1 = os.listdir(folder1)

    # フォルダ2内のフォルダリストを取得
    folders2 = os.listdir(folder2)

    # フォルダ1に存在し、フォルダ2に存在しないフォルダを見つける
    missing_folders = [folder for folder in folders1 if folder not in folders2]

    # 結果を出力
    print(f"フォルダ '{folder1}' にあって '{folder2}' に存在しないフォルダ:")
    for folder in missing_folders:
        print(folder)
    print('FINISH')

# 使用例
folder1_path = '/home/dataset/yyama_dataset/tasks/AC/train'
folder2_path = '/home/dataset/yyama_dataset/tasks/AC/val'
find_missing_folders(folder1_path, folder2_path)
find_missing_folders(folder2_path, folder1_path)

フォルダ '/home/dataset/yyama_dataset/tasks/AC/train' にあって '/home/dataset/yyama_dataset/tasks/AC/val' に存在しないフォルダ:
bronze_medal
cashmere_sweater
concrete_pillar
laptop_casing
notebook
nylon_tent
painted_metal_surface
pin
seal
shampoo_bottle
shaving_cream_can
FINISH
フォルダ '/home/dataset/yyama_dataset/tasks/AC/val' にあって '/home/dataset/yyama_dataset/tasks/AC/train' に存在しないフォルダ:
FINISH


## ○○_instructions.jsonの作成

In [114]:
import os
import json

def natural_sort_key(s):
    """
    ファイル名の数字部分を考慮してソートするためのキー関数
    """
    import re
    return [int(text) if text.isdigit() else text.lower() for text in re.split('(\d+)', s)]

def generate_json_from_directory(directory_path, output_json_path):
    output = {"data": {}}
    i = 0
    # メインディレクトリ内のサブディレクトリを走査
    for main_folder in os.listdir(directory_path):
        main_folder_path = os.path.join(directory_path, main_folder)
        print(f'main folder : {main_folder_path}')
        # サブディレクトリがディレクトリであるかの確認
        if os.path.isdir(main_folder_path):
            
            # サブディレクトリ内のサブディレクトリを走査
            for sub_folder in os.listdir(main_folder_path):
                sub_folder_path = os.path.join(main_folder_path, sub_folder)
                print(f'sub folder : {sub_folder_path}')
                # サブディレクトリ内のファイルを昇順に走査
                for image_file in sorted(os.listdir(sub_folder_path), key=natural_sort_key):
                    # 画像ファイルの拡張子を除去
                    image_name_without_extension = os.path.splitext(image_file)[0]
                    
                    # キーの名前を生成
                    key_name = f"{main_folder}+{sub_folder}+{image_name_without_extension}"
                    print(key_name)
                    # JSONのデータ構造を生成
                    output["data"][key_name] = {
                        "instruction": "",
                        "answer": "",
                        "image_ids": [key_name],
                        "label": i
                    }
                i += 1
    
    # JSONをファイルに書き出し
    with open(output_json_path, "w", encoding="utf-8") as json_file:
        json.dump(output, json_file, indent=4, ensure_ascii=False)

# プログラムの実行
context_path = "/home/dataset/yyama_dataset/tasks/AC/train"
output_json_path = f"/home/dataset/yyama_dataset/tasks/AC/AC_train_instructions.json"
generate_json_from_directory(context_path, output_json_path)

context_path = "/home/dataset/yyama_dataset/tasks/AC/val"
output_json_path = f"/home/dataset/yyama_dataset/tasks/AC/AC_val_instructions.json"
generate_json_from_directory(context_path, output_json_path)

### default用のjsonを作成
context_path = "/home/dataset/yyama_dataset/tasks/AC/train"
output_json_path = f"/home/dataset/yyama_dataset/tasks/AC/default_AC_train_instructions.json"
generate_json_from_directory(context_path, output_json_path)

context_path = "/home/dataset/yyama_dataset/tasks/AC/val"
output_json_path = f"/home/dataset/yyama_dataset/tasks/AC/default_AC_val_instructions.json"
generate_json_from_directory(context_path, output_json_path)

main folder : /home/dataset/yyama_dataset/tasks/AC/train/acrylic_paint
sub folder : /home/dataset/yyama_dataset/tasks/AC/train/acrylic_paint/None
acrylic_paint+None+image_0
acrylic_paint+None+image_1
acrylic_paint+None+image_5
acrylic_paint+None+image_6
acrylic_paint+None+image_7
acrylic_paint+None+image_10
acrylic_paint+None+image_12
acrylic_paint+None+image_18
acrylic_paint+None+image_20
acrylic_paint+None+image_26
acrylic_paint+None+image_38
acrylic_paint+None+image_51
main folder : /home/dataset/yyama_dataset/tasks/AC/train/acrylic_paint_on_canvas
sub folder : /home/dataset/yyama_dataset/tasks/AC/train/acrylic_paint_on_canvas/crack
acrylic_paint_on_canvas+crack+image_0
acrylic_paint_on_canvas+crack+image_2
acrylic_paint_on_canvas+crack+image_3
sub folder : /home/dataset/yyama_dataset/tasks/AC/train/acrylic_paint_on_canvas/fading
acrylic_paint_on_canvas+fading+image_2
acrylic_paint_on_canvas+fading+image_3
acrylic_paint_on_canvas+fading+image_4
acrylic_paint_on_canvas+fading+image_1

### instructionとanswerを埋める

In [115]:
question_lines = [
    ['Are there any defects visible? Please list them if so.'],
    ['Can you spot any defects? Kindly provide the names of any defects.'],
    ['Are any defects present? If so, please specify the defect(s).'],
    ["Is there a defect noticeable? Please mention the defect's name if present."],
    ['Could you point out any defects? If yes, name the defect(s), please.'],
    ['Are there imperfections to be noted? Please identify the defect(s) by name.'],
    ['Could you identify defects? Please specify any defects identified.'],
    ["Is the image showing any defects? If that's the case, please state the defect."],
    ['Are defects evident in this image? Please provide the name of any such defects.'],
    ['Can you detect any defects here? Please detail the defect(s) found.'],
    ['Is this picture defect-free? Please give the name of any defects found.'],
    ['Are there flaws in this image? If any, please provide the defect identification.'],
    ['Does this picture show any defects? Please provide the defect details if applicable.'],
    ['Can you see any defects in this image? Please cite the defect(s) if any.'],
    ['Are defects apparent in this picture? If present, please provide the defect name.'],
    ['Are there any issues with this image? Please state the defect(s) if they exist.'],
    ['Do you find any defects in this image? Please name any defects observed.'],
    ['Could you inspect the image for defects? Please declare any defects noticed.'],
    ['Is the image marred by defects? Please call out any defects detected.'],
    ['Are there any defects that stand out? Please enumerate the defect(s) if any.'],
    ['Is there anything amiss with this image? Please provide the defect name(s) if evident.'],
    ['Would you say there are defects in the image? Please indicate the defect(s) if any are found.'],
    ['Could there be any defects in this image? Please report any defects identified.'],
    ['Are imperfections present in this image? Please name the defect(s) if any are visible.'],
    ['Does this image exhibit any defects? Please describe the defect(s) if present.'],
    ['Might there be defects in this image? Please reveal any defect names if found.'],
    ['Are there noticeable defects in this image? Please disclose any defects if detected.'],
    ['Is anything incorrect with this image? Please point out the defect(s) if any.'],
    ['Can you confirm if there are defects in the image? Please announce the defect(s) if observed.'],
    ['Is the image flawed in any way? Please articulate any defects if any.']
]

yes_responses_array = [
    ['Yes. The product shown has {defect}.'],
    ["Yes. Indeed, there's {defect} evident in the product."],
    ['Yes. Absolutely, {defect} is present in this item.'],
    ['Yes. Certainly, the product displays {defect}.'],
    ['Yes. Affirmative, the item exhibits {defect}.'],
    ['Yes. Correct, {defect} can be seen on the product.'],
    ['Yes. Undoubtedly, the product is marked by {defect}.'],
    ['Yes. Confirmed, we can observe {defect} in the product.'],
    ['Yes. {defect} is visible on this item.'],
    ['Yes. Surely, the product carries {defect}.'],
    ['Yes. The product shown has {defect}.'],
    ["Yes. Indeed, there's {defect} evident in the product."],
    ['Yes. Absolutely, {defect} is present in this item.'],
    ['Yes. Certainly, the product displays {defect}.'],
    ['Yes. Affirmative, the item exhibits {defect}.'],
    ['Yes. Correct, {defect} can be seen on the product.'],
    ['Yes. Undoubtedly, the product is marked by {defect}.'],
    ['Yes. Confirmed, we can observe {defect} in the product.'],
    ['Yes. {defect} is visible on this item.'],
    ['Yes. Surely, the product carries {defect}.'],
    ['Yes. The product shown has {defect}.'],
    ["Yes. Indeed, there's {defect} evident in the product."],
    ['Yes. Absolutely, {defect} is present in this item.'],
    ['Yes. Certainly, the product displays {defect}.'],
    ['Yes. Affirmative, the item exhibits {defect}.'],
    ['Yes. Correct, {defect} can be seen on the product.'],
    ['Yes. Undoubtedly, the product is marked by {defect}.'],
    ['Yes. Confirmed, we can observe {defect} in the product.'],
    ['Yes. {defect} is visible on this item.'],
    ['Yes. Surely, the product carries {defect}.']
]

no_responses_array = [
    ['No. There are no defects in the product depicted.'],
    ['No. Negative, the product shown is devoid of any defects.'],
    ['No. The item does not exhibit any defects.'],
    ['No. Certainly not, the product is without defects.'],
    ['No. I find no defects in this product.'],
    ['No. The product is clear of any defects.'],
    ['No. Upon inspection, no defects are present.'],
    ['No. The item is free from defects.'],
    ['No. No defects are detected in the product.'],
    ['No. The product appears to be defect-free.'],
    ['No. There are no defects in the product depicted.'],
    ['No. Negative, the product shown is devoid of any defects.'],
    ['No. The item does not exhibit any defects.'],
    ['No. Certainly not, the product is without defects.'],
    ['No. I find no defects in this product.'],
    ['No. The product is clear of any defects.'],
    ['No. Upon inspection, no defects are present.'],
    ['No. The item is free from defects.'],
    ['No. No defects are detected in the product.'],
    ['No. The product appears to be defect-free.'],
    ['No. There are no defects in the product depicted.'],
    ['No. Negative, the product shown is devoid of any defects.'],
    ['No. The item does not exhibit any defects.'],
    ['No. Certainly not, the product is without defects.'],
    ['No. I find no defects in this product.'],
    ['No. The product is clear of any defects.'],
    ['No. Upon inspection, no defects are present.'],
    ['No. The item is free from defects.'],
    ['No. No defects are detected in the product.'],
    ['No. The product appears to be defect-free.']
]



In [116]:
import json
import os
import random
import numpy as np


# 指定されたリスト形式の文字列を作成する関数
def generate_list_string(items):
    # アンダースコアをスペースに変換
    items = [item.replace('_', ' ') for item in items]
    
    if len(items) == 1:
        return items[0]
    elif len(items) == 2:
        return f"{items[0]} and {items[1]}"
    else:
        return ", ".join(items[:-1]) + f", and {items[-1]}"

def fill_instruction_and_answer(json_path, train_context_dir,flag=0):
    # JSONを読み込む
    no_count = 0
    yes_count = 0
    random_list = np.zeros(len(question_lines))
    with open(json_path, "r", encoding="utf-8") as f:
        data = json.load(f)["data"]

    # ['data']からキーを順に読み込む
    for key, value in data.items():
        # キーの名前から親フォルダ名と子フォルダ名を認識する
        parent_folder, child_folder, _ = key.split("+")

        # "./1_train_context/親フォルダ名"にアクセスし、その中にある子フォルダ名をリスト化する
        subfolder_list = os.listdir(os.path.join(train_context_dir, parent_folder))
        subfolder_list = [folder for folder in subfolder_list if folder != parent_folder] # 親フォルダ名を除外

        # "instruction"にテキストを入力する
        subfolder_string = generate_list_string(subfolder_list)
        parent_folder__ = parent_folder.replace('_', ' ')
        if flag==0:
            random_idx = random.randint(0, len(question_lines)-1)
            random_list[random_idx] += 1
            value["instruction"] = question_lines[random_idx][0]
        else:
            value["instruction"] = f'Does this image have any defects? If there are any defects, please provide the defect name. If not, please say None.'
       
        # "answer"にテキストを入力する
        if child_folder=="None":
            no_count += 1
            if flag==0:
                value["answer"] = no_responses_array[random_idx][0]
                print(value["answer"])
            else:
                value["answer"] = f'None'
                print(value["answer"])   
        else:
            yes_count += 1
            child_folder = child_folder.replace('_', ' ')
            if flag==0:
                value["answer"] = yes_responses_array[random_idx][0].format(defect=child_folder)
                print(value["answer"])
            else:
                value["answer"] = f'{child_folder}'
                print(value["answer"])
            # print(f"selected answer:  {yes_responses_array[random_idx][0]}")
    print(f"no_count: {no_count}")
    print(f"yes_count: {yes_count}")
    print(f"random_list: {random_list}")

    # JSONをファイルに書き出し
    with open(json_path, "w", encoding="utf-8") as json_file:
        json.dump({"data": data}, json_file, indent=4, ensure_ascii=False)

# プログラムの実行
json_path = f"/home/dataset/yyama_dataset/tasks/AC/AC_train_instructions.json"
dir = "/home/dataset/yyama_dataset/tasks/AC/train"
fill_instruction_and_answer(json_path, dir)

json_path = f"/home/dataset/yyama_dataset/tasks/AC/AC_val_instructions.json"
dir = "/home/dataset/yyama_dataset/tasks/AC/val"
fill_instruction_and_answer(json_path, dir)

### default用の実験
# プログラムの実行
json_path = f"/home/dataset/yyama_dataset/tasks/AC/default_AC_train_instructions.json"
dir = "/home/dataset/yyama_dataset/tasks/AC/train"
fill_instruction_and_answer(json_path, dir,flag=1)

json_path = f"/home/dataset/yyama_dataset/tasks/AC/default_AC_val_instructions.json"
dir = "/home/dataset/yyama_dataset/tasks/AC/val"
fill_instruction_and_answer(json_path, dir,flag=1)

No. The product appears to be defect-free.
No. The item is free from defects.
No. The item does not exhibit any defects.
No. The item is free from defects.
No. The item is free from defects.
No. Upon inspection, no defects are present.
No. The product is clear of any defects.
No. I find no defects in this product.
No. Certainly not, the product is without defects.
No. There are no defects in the product depicted.
No. The item does not exhibit any defects.
No. Negative, the product shown is devoid of any defects.
Yes. crack is visible on this item.
Yes. Certainly, the product displays crack.
Yes. Surely, the product carries crack.
Yes. Indeed, there's fading evident in the product.
Yes. Affirmative, the item exhibits fading.
Yes. Affirmative, the item exhibits fading.
Yes. Undoubtedly, the product is marked by fading.
Yes. fading is visible on this item.
No. There are no defects in the product depicted.
No. I find no defects in this product.
No. Upon inspection, no defects are present.


## ○○_train.jsonの作成

In [117]:
import json
import random

def create_visual_inspection_train(input_json_path, output_json_path):
    # JSONを読み込む
    with open(input_json_path, "r", encoding="utf-8") as f:
        data = json.load(f)["data"]
    # print(data)

    train_data = {}

    # ['data']からキーを順に読み込む
    keys = []
    for key, value in data.items():
        keys.append(key)
        # print(f'key: {key}  value: {value}' )
    
    # ランダムにシャッフルしてデータを保存
    random.shuffle(keys)
    for key_name in keys:
        train_data[f"{key_name}"] = []
        print(key_name)

    # JSONをファイルに書き出し
    with open(output_json_path, "w", encoding="utf-8") as json_file:
        json.dump(train_data, json_file, indent=4, ensure_ascii=False)

# プログラムの実行
input_json_path = f"/home/dataset/yyama_dataset/tasks/AC/AC_train_instructions.json"
output_json_path = f"/home/dataset/yyama_dataset/tasks/AC/AC_train_train.json"
create_visual_inspection_train(input_json_path, output_json_path)

input_json_path = f"/home/dataset/yyama_dataset/tasks/AC/AC_val_instructions.json"
output_json_path = f"/home/dataset/yyama_dataset/tasks/AC/AC_val_train.json"
create_visual_inspection_train(input_json_path, output_json_path)

# プログラムの実行
input_json_path = f"/home/dataset/yyama_dataset/tasks/AC/default_AC_train_instructions.json"
output_json_path = f"/home/dataset/yyama_dataset/tasks/AC/default_AC_train_train.json"
create_visual_inspection_train(input_json_path, output_json_path)

input_json_path = f"/home/dataset/yyama_dataset/tasks/AC/default_AC_val_instructions.json"
output_json_path = f"/home/dataset/yyama_dataset/tasks/AC/default_AC_val_train.json"
create_visual_inspection_train(input_json_path, output_json_path)

tape_dispenser+None+image_40
bronze+tarnish+image_85
woven_basket+None+image_8
marble_floor+crack+image_21
poster+fading+image_5
gold_bar+fading+image_13
pen+None+image_71
metal+scratch+image_82
metal_zipper+None+image_0
concrete_driveway+unevenness+image_3
tape_dispenser+None+image_16
kitchen_faucet+None+image_48
CD_disk+None+image_40
paperback_novel+None+image_8
lens+scratch+image_24
concrete_block+None+image_9
charcoal_sketch+None+image_36
ceramic_mug+broken+image_16
knife_blade+None+image_16
disk+broken+image_17
rod+corrosion+image_2
chip+None+image_58
book_cover+None+image_2
leather+scratch+image_104
window+fog+image_5
concrete_wall+stain+image_32
whisk+None+image_19
power_socket+burn+image_28
door+None+image_5
aluminum+scratch+image_41
aluminum_foil+wrinkle+image_21
knife+None+image_17
marble+discoloration+image_19
ceramic_tiles+None+image_16
rubber_ball+None+image_8
bag+mold+image_4
carpet+fading+image_5
woven_rug+None+image_33
hard_disk_drive+None+image_42
aluminum_ladder+None+

In [118]:
# 数の確認
json_path = f"/home/dataset/yyama_dataset/tasks/AC/AC_train_train.json"

with open(json_path, "r", encoding="utf-8") as f:
    data = json.load(f)
    
count = len(data.keys())
print(f"データ数: {count}")

json_path = f"/home/dataset/yyama_dataset/tasks/AC/AC_val_train.json"

with open(json_path, "r", encoding="utf-8") as f:
    data = json.load(f)
    
count = len(data.keys())
print(f"データ数: {count}")

# 数の確認
json_path = f"/home/dataset/yyama_dataset/tasks/AC/default_AC_train_train.json"

with open(json_path, "r", encoding="utf-8") as f:
    data = json.load(f)
    
count = len(data.keys())
print(f"データ数: {count}")

json_path = f"/home/dataset/yyama_dataset/tasks/AC/default_AC_val_train.json"

with open(json_path, "r", encoding="utf-8") as f:
    data = json.load(f)
    
count = len(data.keys())
print(f"データ数: {count}")

データ数: 15271
データ数: 3828
データ数: 15271
データ数: 3828


## ○○.jsonの作成

In [2]:
import json
import os
from PIL import Image
import io
import base64

# コンテキスト　→　クエリの順で実行すること

def image_to_urlsafe_base64_png(img_path):
    """画像をメモリ上でPNGに変換し、その後URL-safeなBase64に変換する関数"""
    with Image.open(img_path) as image:
        # CMYKモードの画像をRGBモードに変換
        if image.mode == 'CMYK':
            image = image.convert('RGB')
        # パレットモードの画像をRGBAモードに変換
        if image.mode == 'P':
            image = image.convert('RGBA')
        buffered = io.BytesIO()
        image.save(buffered, format="PNG")
        img_str = base64.urlsafe_b64encode(buffered.getvalue()).decode('utf-8')
    return img_str

def create_visual_inspection(input_json_path, base_folder, output_json_path):
    # JSONを読み込む
    with open(input_json_path, "r", encoding="utf-8") as f:
        data = json.load(f)["data"]

    # 既存のvisual_inspection.jsonが存在する場合、その内容を読み込む
    if os.path.exists(output_json_path):
        with open(output_json_path, "r", encoding="utf-8") as f:
            visual_data = json.load(f)
    else:
        visual_data = {}

    extensions = ['.png', '.jpg', '.jpeg','JPEG','.JPG','.PNG']

    # ['data']からキーを順に読み込む
    for key in data.keys():
        parent_folder, child_folder, image_name = key.split("+")
        
        # 各拡張子を試して、存在するファイルを見つける
        for ext in extensions:
            img_path = os.path.join(base_folder, parent_folder, child_folder, image_name + ext)
            if os.path.exists(img_path):
                # 画像をURL-safeなBase64 PNG形式に変換
                # print(img_path)
                visual_data[key] = image_to_urlsafe_base64_png(img_path)
                break

    # JSONをファイルに書き出し
    with open(output_json_path, "w", encoding="utf-8") as json_file:
        json.dump(visual_data, json_file, indent=4, ensure_ascii=False)

# プログラムの実行
# base_folder = "/home/dataset/yyama_dataset/tasks/AC/train"  # これは一つ上のベースフォルダのパス
# input_json_path = "/home/dataset/yyama_dataset/tasks/AC/AC_train_instructions.json"
# output_json_path = f"/home/dataset/yyama_dataset/tasks/AC/AC_train.json"
# create_visual_inspection(input_json_path, base_folder, output_json_path)
# print(f'finish making train.json')

# base_folder = "/home/dataset/yyama_dataset/tasks/AC/val"  # これは一つ上のベースフォルダのパス
# input_json_path = "/home/dataset/yyama_dataset/tasks/AC/AC_val_instructions.json"
# output_json_path = f"/home/dataset/yyama_dataset/tasks/AC/AC_val.json"
# create_visual_inspection(input_json_path, base_folder, output_json_path)
# print(f'finish making val.json')

base_folder = "/home/dataset/yyama_dataset/tasks/AC/train"  # これは一つ上のベースフォルダのパス
input_json_path = "/home/dataset/yyama_dataset/tasks/AC/default_AC_train_instructions.json"
output_json_path = f"/home/dataset/yyama_dataset/tasks/AC/default_AC_train.json"
create_visual_inspection(input_json_path, base_folder, output_json_path)
print(f'finish making default train.json')
base_folder = "/home/dataset/yyama_dataset/tasks/AC/val"  # これは一つ上のベースフォルダのパス
input_json_path = "/home/dataset/yyama_dataset/tasks/AC/default_AC_val_instructions.json"
output_json_path = f"/home/dataset/yyama_dataset/tasks/AC/default_AC_val.json"
create_visual_inspection(input_json_path, base_folder, output_json_path)
print(f'finish making default val.json')

finish making default train.json
finish making default val.json


In [37]:
import json

# 数の確認
json_path = "/home/dataset/yyama_dataset/tasks/AC/AC_train.json"

with open(json_path, "r", encoding="utf-8") as f:
    data = json.load(f)
    
count = len(data.keys())
print(f"train画像枚数: {count}")

json_path = "/home/dataset/yyama_dataset/tasks/AC/AC_val.json"

with open(json_path, "r", encoding="utf-8") as f:
    data = json.load(f)
    
count = len(data.keys())
print(f"val画像枚数: {count}")

train画像枚数: 14424
val画像枚数: 4487
